# Introduction

> The script automates gathering of tweet data from the archives

## Packages

In [1]:
#import packages 
import pandas as pd 
import numpy as np
import os 
import time
import requests
import itertools    
import json
import re

from datetime import date
from datetime import datetime
from datetime import timedelta

#import data scraping packages 
import tweepy
# from tweepy.streaming import StreamListener
from tweepy import OAuthHandler
from tweepy import Stream
from tweepy import Cursor
from tweepy import API

#import web scrapping packages 
import bs4 as bs
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import chromedriver_autoinstaller
from selenium_stealth import stealth
import undetected_chromedriver as uc



#sns module 
import snscrape.modules.twitter as sntwitter
import snscrape.modules.facebook as snfacebook
import snscrape.modules.instagram as sninstagram

#postgresql database packages 
import psycopg2
import psycopg2.extras as extras
from sqlalchemy import create_engine

import csv
from io import StringIO

#check the start time
start_time = datetime.now()

## Extract Time

In [2]:
#generate the 
number_of_dates = 365*5
end_date = date.today()
start_date =  end_date - timedelta(days=number_of_dates)
duration = end_date - start_date

print()
print()
print(f"The start date: {start_date} end date is: {end_date} and time duration is: {duration}")



The start date: 2017-08-24 end date is: 2022-08-23 and time duration is: 1825 days, 0:00:00


In [3]:
#get todays date
today = datetime.now()

# format the dates
formated_date = today.strftime("%B %d %Y %H %M %S")

#print date 
print()
print()
print("Todays date: ", formated_date)



Todays date:  August 23 2022 20 46 51


### Keywords

> The following are search keywords for cyber security concerns 

In [4]:
#define variables 
keywords_list = ["Trojan", "Spyware", "ransomware", "Botnet", "Defense", "Evasion","ingress tool transfer", "Malicious link","firmware", "Bruteforce", "automated exfiltration", 
                 "DNSSEC traffic", "channel attacks", "DHCP spoofing","Protocol impersonation", "Denial of Service", "Phishing", "Spearphishing", "OS Credential Dumping"]

#search words 
#fornat the sland 
print()
print()
print(f"{'*'*50} Keyword list {'*'*60}")
print(keywords_list)

print()
print()
#search words 
print(f"{'*'*50} Joined Keyword List {'*'*50}")
search_word = "|".join([j.lower() for j in keywords_list])
print(search_word)





************************************************** Keyword list ************************************************************
['Trojan', 'Spyware', 'ransomware', 'Botnet', 'Defense', 'Evasion', 'ingress tool transfer', 'Malicious link', 'firmware', 'Bruteforce', 'automated exfiltration', 'DNSSEC traffic', 'channel attacks', 'DHCP spoofing', 'Protocol impersonation', 'Denial of Service', 'Phishing', 'Spearphishing', 'OS Credential Dumping']


************************************************** Joined Keyword List **************************************************
trojan|spyware|ransomware|botnet|defense|evasion|ingress tool transfer|malicious link|firmware|bruteforce|automated exfiltration|dnssec traffic|channel attacks|dhcp spoofing|protocol impersonation|denial of service|phishing|spearphishing|os credential dumping


### African Countries

In [5]:
#countries involved
name = ['Algeria','Angola','Benin','Botswana','Burkina_Faso','Burundi','Cameroon','Cape_Verde',
             'Central_African_Republic','Chad','Comoros','Democratic_Republic_of_the_Congo','Djibouti','Egypt',
             'Equatorial_Guinea',' Eritrea',' Ethiopia',' Gabon',' Gambia',' Ghana','Guinea',' Guinea-Bissau',
             'Ivory_Coast','Kenya',' Lesotho',' Liberia',' Libya',' Madagascar',' Malawi',' Mali',' Mauritania','Mauritius',
             'Morocco',' Mozambique',' Namibia',' Niger',' Nigeria','Republic of the Congo',' Rwanda','Sao_Tome_and_Principe',
             'Senegal',' Seychelles',' Sierra_Leone',' Somalia',' South_Africa',' Sudan','South_Sudan','Swaziland',' Tanzania',' Togo',
             'Tunisia',' Uganda',' Zambia',' Zimbabwe']

# #strip any white spaces 
country_name = [x.strip().lower().replace('_','-').replace(' ','-') for x in name]

#search words 
countries = "|".join([j.strip().lower() for j in name])

In [6]:
options = webdriver.ChromeOptions()
options.add_argument("start-maximized")
options.add_argument("--headless")
options.add_experimental_option("excludeSwitches", ["enable-automation"])
options.add_experimental_option('useAutomationExtension', False)

In [7]:
 driver = webdriver.Chrome(r'C:\Users\chromedriver_win32\chromedriver.exe')

C:\Users\moses\AppData\Local\Temp\ipykernel_17148\1516475625.py:1: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(r'C:\Users\chromedriver_win32\chromedriver.exe')


In [24]:
keywkeywords_listist

19

## Place Specific 

> Countries towns and cities co-ordinates [link](https://www.countrycoordinate.com/)

In [8]:
#get the data in a dataframe 
coordinates_df =  pd.DataFrame()
count = 0

for country in country_name:
    #get the url
    url = f"https://www.countrycoordinate.com/country-{country}/"
    count +=1
    print(f"Num: {count}; link: {url}") 
    try:
        driver = uc.Chrome(use_subprocess=True)
        driver.get(url)
        time.sleep(5)
        soup = bs.BeautifulSoup(driver.page_source,'lxml')

        # get data table & save as dataframe
        table_val = soup.find("table",{'table table-bordered table-hover'})
        table_val_df = pd.read_html(str(table_val))[0]

        table_val_df.columns = ['city', 'coords']
        table_val_df['country'] = country
        table_val_df['url'] = url
        table_val_df[['lat', 'lon']] = table_val_df['coords'].str.split('/', expand = True)
        table_val_df.drop(columns = ['coords'], inplace = True)
        if table_val_df.shape[0]>1:
            coordinates_df = pd.concat([coordinates_df,table_val_df])
        else:
            pass


        #get the number of other pages 
        page_num_table = soup.find_all("table", {"class":"table table-bordered centered"})



          #loop through other pages
        print(f"{'*'*15} base page done {'*'*15}")
        print(f"{'*'*15} Other pages {'*'*15}")
        for tab in page_num_table:
            row = tab.find_all('a')
            row = [i.text.strip() for i in row]
            row = row[:-1]
            print(f"{'*'*15} pages to extract {len(row)+1} {'*'*15}")

            for page in row: 
                next_page_url = url+f"?page={page}"
                print(next_page_url)

                #get the data 
                driver.get(next_page_url)
                time.sleep(2)
                soup_page = bs.BeautifulSoup(driver.page_source, 'lxml')

                # get data table & save as dataframe
                table_val_next = soup_page.find("table",{'table table-bordered table-hover'})
                table_val_df_1 = pd.read_html(str(table_val_next))[0]
                table_val_df_1.columns = ['city', 'coords']
                table_val_df_1['country'] = country
                table_val_df_1['url'] = url
                table_val_df_1[['lat', 'lon']] = table_val_df_1['coords'].str.split('/', expand = True)
                table_val_df_1.drop(columns = ['coords'], inplace = True)
                if table_val_df_1.shape[0]>1:
                    coordinates_df = pd.concat([coordinates_df,table_val_df_1])
                else:
                    pass
                
    except Exception as e:
        print(f'The error is: {str(e)}')
        pass
    
#clean the data 

#reset the index
coordinates_df.reset_index(drop = True, inplace = True)

#clean the data 
coordinates_df['city'] = coordinates_df['city'].str.split('(', expand = True)[0]

#drop duplicate towns
print(f"Rows before droping duplicates {coordinates_df.shape[0]}")
coordinates_df.drop_duplicates(subset = ['city', 'country'], inplace = True, keep = 'last')
print(f"Rows befor droping duplicates {coordinates_df.shape[0]}")

#print the sample 
coordinates_df.sample(3)

Num: 1; link: https://www.countrycoordinate.com/country-algeria/
*************** base page done ***************
*************** Other pages ***************
*************** pages to extract 7 ***************
https://www.countrycoordinate.com/country-algeria/?page=2
https://www.countrycoordinate.com/country-algeria/?page=3
https://www.countrycoordinate.com/country-algeria/?page=4
https://www.countrycoordinate.com/country-algeria/?page=5
https://www.countrycoordinate.com/country-algeria/?page=12
https://www.countrycoordinate.com/country-algeria/?page=13
Num: 2; link: https://www.countrycoordinate.com/country-angola/
*************** base page done ***************
*************** Other pages ***************
*************** pages to extract 2 ***************
https://www.countrycoordinate.com/country-angola/?page=2
Num: 3; link: https://www.countrycoordinate.com/country-benin/
*************** base page done ***************
*************** Other pages ***************
*************** pages to e

*************** base page done ***************
*************** Other pages ***************
*************** pages to extract 3 ***************
https://www.countrycoordinate.com/country-libya/?page=2
https://www.countrycoordinate.com/country-libya/?page=3
Num: 28; link: https://www.countrycoordinate.com/country-madagascar/
*************** base page done ***************
*************** Other pages ***************
*************** pages to extract 6 ***************
https://www.countrycoordinate.com/country-madagascar/?page=2
https://www.countrycoordinate.com/country-madagascar/?page=3
https://www.countrycoordinate.com/country-madagascar/?page=4
https://www.countrycoordinate.com/country-madagascar/?page=5
https://www.countrycoordinate.com/country-madagascar/?page=6
Num: 29; link: https://www.countrycoordinate.com/country-malawi/
*************** base page done ***************
*************** Other pages ***************
*************** pages to extract 2 ***************
https://www.countrycoor

Num: 52; link: https://www.countrycoordinate.com/country-uganda/
*************** base page done ***************
*************** Other pages ***************
*************** pages to extract 4 ***************
https://www.countrycoordinate.com/country-uganda/?page=2
https://www.countrycoordinate.com/country-uganda/?page=3
https://www.countrycoordinate.com/country-uganda/?page=4
Num: 53; link: https://www.countrycoordinate.com/country-zambia/
*************** base page done ***************
*************** Other pages ***************
*************** pages to extract 4 ***************
https://www.countrycoordinate.com/country-zambia/?page=2
https://www.countrycoordinate.com/country-zambia/?page=3
https://www.countrycoordinate.com/country-zambia/?page=4
Num: 54; link: https://www.countrycoordinate.com/country-zimbabwe/
*************** base page done ***************
*************** Other pages ***************
*************** pages to extract 3 ***************
https://www.countrycoordinate.com/c

city                   country  \
576     Ḏânan                  djibouti   
2333  Kirando                  tanzania   
475     Kembé  central-african-republic   

                                                    url         lat  \
576   https://www.countrycoordinate.com/country-djib...  11.183333    
2333  https://www.countrycoordinate.com/country-tanz...  -2.806961    
475   https://www.countrycoordinate.com/country-cent...   4.614737    

             lon  
576    42.933333  
2333   33.991722  
475    21.886668

> Extract tweets with keywords

In [13]:
#create and empty df
df_x = pd.DataFrame()

#define the max keywords
maxcounts = 200
count = 0

try: 
    for row in coordinates_df.index:
            country = coordinates_df['country'][row]
            nearby_location = coordinates_df['city'][row]
            lat = coordinates_df['lat'][row]
            lon = coordinates_df['lon'][row]
            circumfrence = "20km"
            coor = lat+","+lon+","+circumfrence
            coor = format(coor)
            print()
            print(f"country: {country}, nearby_loc: {nearby_location},  coordinates: {lat+', '+lon}, radius: {circumfrence}")
            
            try:
                for word in keywords_list:
                    count +=1
                    
                    print(f"{'*'*20} instance within: {count};  word: {word} {'*'*20}")
                    scraped_tweets = sntwitter.TwitterSearchScraper(f'{str(word)} since:{start_date} until:{end_date} geocode:"{coor}"').get_items()

                    sliced_scraped_tweets = itertools.islice(scraped_tweets, maxcounts)  
                    df_coord = pd.DataFrame(sliced_scraped_tweets)
                    df_coord.columns = df_coord.columns.str.lower()
                    df_coord['keyword'] = word
                    df_coord['nearby_location'] = nearby_location
                    df_coord['country'] = country
                    df_x = pd.concat([df_x, df_coord])
                    
            except Exception as e:
                print(f'The error was: {str(e)}')
except Exception as e:
    print(f'The error was: {str(e)}')


country: algeria, nearby_loc: Algiers,  coordinates: 36.753768 ,  3.058756, radius: 20km
******************** num: 1;  word: Trojan ********************
******************** num: 2;  word: Spyware ********************
******************** num: 3;  word: ransomware ********************
******************** num: 4;  word: Botnet ********************
******************** num: 5;  word: Defense ********************
******************** num: 6;  word: Evasion ********************
******************** num: 7;  word: ingress tool transfer ********************
******************** num: 8;  word: Malicious link ********************
******************** num: 9;  word: firmware ********************
******************** num: 10;  word: Bruteforce ********************
******************** num: 11;  word: automated exfiltration ********************
******************** num: 12;  word: DNSSEC traffic ********************
******************** num: 13;  word: channel attacks ********************
*****

******************** num: 109;  word: DHCP spoofing ********************
******************** num: 110;  word: Protocol impersonation ********************
******************** num: 111;  word: Denial of Service ********************
******************** num: 112;  word: Phishing ********************
******************** num: 113;  word: Spearphishing ********************
******************** num: 114;  word: OS Credential Dumping ********************

country: algeria, nearby_loc: Sétif,  coordinates: 36.196903 ,  5.415087, radius: 20km
******************** num: 115;  word: Trojan ********************
******************** num: 116;  word: Spyware ********************
******************** num: 117;  word: ransomware ********************
******************** num: 118;  word: Botnet ********************
******************** num: 119;  word: Defense ********************
******************** num: 120;  word: Evasion ********************
******************** num: 121;  word: ingress tool tran

******************** num: 215;  word: Evasion ********************
******************** num: 216;  word: ingress tool transfer ********************
******************** num: 217;  word: Malicious link ********************
******************** num: 218;  word: firmware ********************
******************** num: 219;  word: Bruteforce ********************
******************** num: 220;  word: automated exfiltration ********************
******************** num: 221;  word: DNSSEC traffic ********************
******************** num: 222;  word: channel attacks ********************
******************** num: 223;  word: DHCP spoofing ********************
******************** num: 224;  word: Protocol impersonation ********************
******************** num: 225;  word: Denial of Service ********************
******************** num: 226;  word: Phishing ********************
******************** num: 227;  word: Spearphishing ********************
******************** num: 228;  word

******************** num: 322;  word: Spearphishing ********************
******************** num: 323;  word: OS Credential Dumping ********************

country: algeria, nearby_loc: Skikda,  coordinates: 36.871520 ,  6.910181, radius: 20km
******************** num: 324;  word: Trojan ********************
******************** num: 325;  word: Spyware ********************
******************** num: 326;  word: ransomware ********************
******************** num: 327;  word: Botnet ********************
******************** num: 328;  word: Defense ********************
******************** num: 329;  word: Evasion ********************
******************** num: 330;  word: ingress tool transfer ********************
******************** num: 331;  word: Malicious link ********************
******************** num: 332;  word: firmware ********************
******************** num: 333;  word: Bruteforce ********************
******************** num: 334;  word: automated exfiltration 

******************** num: 428;  word: Bruteforce ********************
******************** num: 429;  word: automated exfiltration ********************
******************** num: 430;  word: DNSSEC traffic ********************
******************** num: 431;  word: channel attacks ********************
******************** num: 432;  word: DHCP spoofing ********************
******************** num: 433;  word: Protocol impersonation ********************
******************** num: 434;  word: Denial of Service ********************
******************** num: 435;  word: Phishing ********************
******************** num: 436;  word: Spearphishing ********************
******************** num: 437;  word: OS Credential Dumping ********************

country: algeria, nearby_loc: Médéa,  coordinates: 36.285385 ,  2.768025, radius: 20km
******************** num: 438;  word: Trojan ********************
******************** num: 439;  word: Spyware ********************
******************** num

...

******************** num: 52026;  word: automated exfiltration ********************
******************** num: 52027;  word: DNSSEC traffic ********************
******************** num: 52028;  word: channel attacks ********************
******************** num: 52029;  word: DHCP spoofing ********************
******************** num: 52030;  word: Protocol impersonation ********************
******************** num: 52031;  word: Denial of Service ********************
******************** num: 52032;  word: Phishing ********************
******************** num: 52033;  word: Spearphishing ********************
******************** num: 52034;  word: OS Credential Dumping ********************

country: zimbabwe, nearby_loc: Mashava,  coordinates: -20.051139 ,  30.510637, radius: 20km
******************** num: 52035;  word: Trojan ********************
******************** num: 52036;  word: Spyware ********************
******************** num: 52037;  word: ransomware ****************


country: zimbabwe, nearby_loc: Banket,  coordinates: -17.379339 ,  30.395428, radius: 20km
******************** num: 52130;  word: Trojan ********************
******************** num: 52131;  word: Spyware ********************
******************** num: 52132;  word: ransomware ********************
******************** num: 52133;  word: Botnet ********************
******************** num: 52134;  word: Defense ********************
******************** num: 52135;  word: Evasion ********************
******************** num: 52136;  word: ingress tool transfer ********************
******************** num: 52137;  word: Malicious link ********************
******************** num: 52138;  word: firmware ********************
******************** num: 52139;  word: Bruteforce ********************
******************** num: 52140;  word: automated exfiltration ********************
******************** num: 52141;  word: DNSSEC traffic ********************
******************** num: 52142;

******************** num: 52233;  word: firmware ********************
******************** num: 52234;  word: Bruteforce ********************
******************** num: 52235;  word: automated exfiltration ********************
******************** num: 52236;  word: DNSSEC traffic ********************
******************** num: 52237;  word: channel attacks ********************
******************** num: 52238;  word: DHCP spoofing ********************
******************** num: 52239;  word: Protocol impersonation ********************
******************** num: 52240;  word: Denial of Service ********************
******************** num: 52241;  word: Phishing ********************
******************** num: 52242;  word: Spearphishing ********************
******************** num: 52243;  word: OS Credential Dumping ********************

country: zimbabwe, nearby_loc: Mangula,  coordinates: -16.898679 ,  30.164704, radius: 20km
******************** num: 52244;  word: Trojan ***************

******************** num: 52337;  word: Spearphishing ********************
******************** num: 52338;  word: OS Credential Dumping ********************

country: zimbabwe, nearby_loc: Mvuma,  coordinates: -19.277369 ,  30.525031, radius: 20km
******************** num: 52339;  word: Trojan ********************
******************** num: 52340;  word: Spyware ********************
******************** num: 52341;  word: ransomware ********************
******************** num: 52342;  word: Botnet ********************
******************** num: 52343;  word: Defense ********************
******************** num: 52344;  word: Evasion ********************
******************** num: 52345;  word: ingress tool transfer ********************
******************** num: 52346;  word: Malicious link ********************
******************** num: 52347;  word: firmware ********************
******************** num: 52348;  word: Bruteforce ********************
******************** num: 52349;  w

******************** num: 52440;  word: ingress tool transfer ********************
******************** num: 52441;  word: Malicious link ********************
******************** num: 52442;  word: firmware ********************
******************** num: 52443;  word: Bruteforce ********************
******************** num: 52444;  word: automated exfiltration ********************
******************** num: 52445;  word: DNSSEC traffic ********************
******************** num: 52446;  word: channel attacks ********************
******************** num: 52447;  word: DHCP spoofing ********************
******************** num: 52448;  word: Protocol impersonation ********************
******************** num: 52449;  word: Denial of Service ********************
******************** num: 52450;  word: Phishing ********************
******************** num: 52451;  word: Spearphishing ********************
******************** num: 52452;  word: OS Credential Dumping *****************

In [25]:
df_x.head(5)

keyword nearby_location  country  \
0     Spyware         Algiers  country   
0  ransomware         Algiers  country   
0      Botnet         Algiers  country   
0     Defense         Algiers  country   
1     Defense         Algiers  country   

                                                 url  \
0  https://twitter.com/abdennour68/status/1420750...   
0  https://twitter.com/ClioVip/status/10717673779...   
0  https://twitter.com/HichamBABAAHMED/status/129...   
0  https://twitter.com/Milanista__1989/status/156...   
1  https://twitter.com/achrafNR06/status/15616374...   

                       date  \
0 2021-07-29 14:19:04+00:00   
0 2018-12-09 14:03:50+00:00   
0 2020-08-20 14:48:28+00:00   
0 2022-08-22 18:39:27+00:00   
1 2022-08-22 08:52:42+00:00   

                                             content  \
0  La società per azioni proprietaria della socie...   
0  @Ros_Bencharif @muratguiddini Chez nous on a p...   
0  @mhsoufi « Un portail de l’Agence du revenu du...   
0  @MilanActuFR J'ai trouvé l'équipe bien en plac...   
1  @Farret13Tejeda mount and havertz choose games...   

                                     renderedcontent            id  \
0  La società per azioni proprietaria della socie...  1.420751e+18   
0  @Ros_Bencharif @muratguiddini Chez nous on a p...  1.071767e+18   
0  @mhsoufi « Un portail de l’Agence du revenu du...  1.296459e+18   
0  @MilanActuFR J'ai trouvé l'équipe bien en plac...  1.561785e+18   
1  @Farret13Tejeda mount and havertz choose games...  1.561637e+18   

                                                user  replycount  ...  media  \
0  {'username': 'abdennour68', 'id': 2174776405, ...         0.0  ...   None   
0  {'username': 'ClioVip', 'id': 1104601712, 'dis...         1.0  ...   None   
0  {'username': 'HichamBABAAHMED', 'id': 60459000...         1.0  ...   None   
0  {'username': 'Milanista__1989', 'id': 15268365...         0.0  ...   None   
1  {'username': 'achrafNR06', 'id': 855223262, 'd...         1.0  ...   None   

   retweetedtweet  quotedtweet       inreplytotweetid  \
0            None         None                   None   
0            None         None    1071674258424778754   
0            None         None    1296452897941708801   
0            None         None  1561639072111681536.0   
1            None         None  1561484655362179072.0   

                                       inreplytouser  \
0                                               None   
0  {'username': 'Ros_Bencharif', 'id': 2827110663...   
0  {'username': 'mhsoufi', 'id': 405384017, 'disp...   
0  {'username': 'MilanActuFR', 'id': 2725435234, ...   
1  {'username': 'Farret13Tejeda', 'id': 100868103...   

                                      mentionedusers  \
0                                               None   
0  [{'username': 'Ros_Bencharif', 'id': 282711066...   
0  [{'username': 'mhsoufi', 'id': 405384017, 'dis...   
0  [{'username': 'MilanActuFR', 'id': 2725435234,...   
1  [{'username': 'Farret13Tejeda', 'id': 10086810...   

                                         coordinates  \
0  {'longitude': 3.08879799966998, 'latitude': 36...   
0  {'longitude': 3.05301324937448, 'latitude': 36...   
0  {'longitude': 2.79962622486003, 'latitude': 36...   
0                                               None   
1                                               None   

                                               place hashtags cashtags  
0  {'fullName': 'El Harrach                      ...     None     None  
0  {'fullName': 'Hussein Dey                     ...     None     None  
0  {'fullName': 'Alger                           ...     None     None  
0                                               None     None     None  
1                                               None     None     None  

[5 rows x 30 columns]

In [27]:
df_x.columns

Index(['keyword', 'nearby_location', 'country', 'url', 'date', 'content',
       'renderedcontent', 'id', 'user', 'replycount', 'retweetcount',
       'likecount', 'quotecount', 'conversationid', 'lang', 'source',
       'sourceurl', 'sourcelabel', 'outlinks', 'tcooutlinks', 'media',
       'retweetedtweet', 'quotedtweet', 'inreplytotweetid', 'inreplytouser',
       'mentionedusers', 'coordinates', 'place', 'hashtags', 'cashtags'],
      dtype='object')

> Clean the extracted tweets

In [31]:

#subset the data
df = df_x[['id', 'date', 'content', 'renderedcontent', 'user', 'replycount','retweetcount', 'likecount', 'quotecount',
           'url', 'lang', 'retweetedtweet', 'quotedtweet','mentionedusers', 'coordinates', 'place', 'hashtags', 'keyword', 
           'nearby_location', 'country']]

#format the date
df['date'] = df['date'].apply(lambda x: x.strftime("%d-%b-%Y %H:%M:%S"))

# getting user's location
df.reset_index(drop = True, inplace = True)
df['username'] = df['user'].apply(lambda x: x['username'])
df['displayname'] = df['user'].apply(lambda x: x['displayname'])
df['user_id'] = df['user'].apply(lambda x: x['id'])
df['user_location'] = df['user'].apply(lambda x: x['location'])
df['description'] = df['user'].apply(lambda x: x['description'])
df['followersCount'] = df['user'].apply(lambda x: x['followersCount'])
df['friendsCount'] = df['user'].apply(lambda x: x['friendsCount'])
df['statusesCount'] = df['user'].apply(lambda x: x['statusesCount'])
df['favouritesCount'] = df['user'].apply(lambda x: x['favouritesCount'])
df['protected'] = df['user'].apply(lambda x: x['protected'])

#mentions 
pattern_1 = r'#(\w+)'
pattern_2 = r'@(\w+)'
# df['hashtag'] = df['content'].apply(lambda x: re.findall(pattern_1, x))
df['mentions'] = df['content'].apply(lambda x: re.findall(pattern_2, x))

#drop some columns 
df.drop(columns = ['user', 'mentionedusers'], inplace = True)


#clean the data 
##lower the text
df['content'] = df['content'].apply(lambda x: x.lower())
df['content'] = df['content'].apply(lambda x: x.strip())
df['content'] = df['content'].apply(lambda x: x.replace("  ", " "))
df['content'] = df['content'].apply(lambda x: x.replace("\n", ""))

##strip white spaces 
df.columns = df.columns.str.strip()

#lower all the names 
df.colums = df.columns.str.lower()


#filter words that contained in the list 
df['search_word'] = np.where(df['content'].str.contains(search_word),'Yes','No')

##drop duplicate tweets if any 
print(f'The number of tweets before droping duplicates are: {df.shape[0]}')
df = df.drop_duplicates(subset=['date', 'id', 'content', 'username', 'user_location', 'renderedcontent', 'keyword', 'lang', 'url', 'user_id'], keep= 'last')
print(f'The number of tweets after droping duplicates are: {df.shape[0]}')

#print the data
df.sample(5)


C:\Users\moses\AppData\Local\Temp\ipykernel_17148\4275255497.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['date'] = df['date'].apply(lambda x: x.strftime("%d-%b-%Y %H:%M:%S"))
C:\Users\moses\AppData\Local\Temp\ipykernel_17148\4275255497.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['username'] = df['user'].apply(lambda x: x['username'])
C:\Users\moses\AppData\Local\Temp\ipykernel_17148\4275255497.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

The number of tweets before droping duplicates are: 67584
The number of tweets after droping duplicates are: 24665


id                  date  \
60693  1.005533e+18  09-Jun-2018 19:30:45   
2639   1.519060e+18  26-Apr-2022 21:06:39   
35700  1.254801e+18  27-Apr-2020 15:54:28   
13859  1.561800e+18  22-Aug-2022 19:39:35   
17619  1.371215e+18  14-Mar-2021 21:41:05   

                                                 content  \
60693  le couloir gauche en défense, on en parle ? #t...   
2639   loukan machi defense goufrita benz would’ve cl...   
35700  @deji_bounty @baller_tinubu @ibukun_m lithium ...   
13859  manchester united really took a leaf of their ...   
17619  @luqmangedi @analystsomalia @cij_icj if somali...   

                                         renderedcontent  replycount  \
60693  Le couloir gauche en défense, on en parle ? \n...         2.0   
2639   Loukan machi defense goufrita Benz would’ve cl...         1.0   
35700  @Deji_bounty @Baller_Tinubu @Ibukun_M Lithium ...         0.0   
13859  Manchester united really took a leaf of their ...         0.0   
17619  @luqmangedi @AnalystSomalia @CIJ_ICJ If Somali...         0.0   

       retweetcount  likecount  quotecount  \
60693           0.0        1.0         0.0   
2639            0.0       14.0         0.0   
35700           1.0        1.0         0.0   
13859           0.0        3.0         0.0   
17619           0.0        1.0         0.0   

                                                     url lang  ...  \
60693  https://twitter.com/YssemSaadi/status/10055326...   fr  ...   
2639   https://twitter.com/TweettsZack/status/1519060...   en  ...   
35700  https://twitter.com/e_akale/status/12548010933...   en  ...   
13859  https://twitter.com/kwekusuwiidey/status/15618...   en  ...   
17619  https://twitter.com/cabdicasis_1/status/137121...   en  ...   

                   user_id        user_location  \
60693             18733589              Tunisia   
2639   1262244631909195776              Algérie   
35700           3064624360  FCT Abuja, Nigeria    
13859   998888286461579265          Tema, Ghana   
17619           3017425216                        

                                             description followersCount  \
60693  Inventive Mind, Empathic Thinker, Lego collect...           9643   
2639                                                                515   
35700             |.E=mc2.| |kWh|DRE|EMS|EE |Smart Grids           2010   
13859                           @KinaataGh ❤️ @chelseafc           2055   
17619           Everything I Retweet has my endorsement.            791   

      friendsCount statusesCount favouritesCount protected  \
60693         1786         19099            1249     False   
2639          1372          3754            1728     False   
35700         1741         77365           36760     False   
13859         2269          6378           14855     False   
17619          525          1879           80660     False   

                                     mentions search_word  
60693                                      []          No  
2639                                       []         Yes  
35700  [Deji_bounty, Baller_Tinubu, Ibukun_M]         Yes  
13859                                      []         Yes  
17619   [luqmangedi, AnalystSomalia, CIJ_ICJ]         Yes  

[5 rows x 30 columns]

> Tweets containing keywords

In [32]:
df['search_word'].value_counts(normalize = True).mul(100).round(1).astype(str) + '%'

Yes    83.2%
No     16.8%
Name: search_word, dtype: object

> Drop the tweets that do not have the keywords

In [33]:
#filter out the only data with matching keyword
data = df[df['search_word']!='No']
data.reset_index(drop = True, inplace = True)
data.head(5)

id                  date  \
0  1.557772e+18  11-Aug-2022 16:51:36   
1  1.147958e+18  07-Jul-2019 19:59:36   
2  1.252676e+18  21-Apr-2020 19:09:14   
3  1.560295e+18  18-Aug-2022 15:59:26   
4  9.548473e+17  20-Jan-2018 22:45:11   

                                             content  \
0  @h_soufiane_dz @defense_news نعم وهوا كذالك ال...   
1                      attaque defense attal❤️❤️🇩🇿🇩🇿   
2  conditions générales d'utilisation (cgu) https...   
3  @statmuse 24.5 ppg8.9 rpg2.1 bpg52/38/92%all s...   
4  @desir_evasion tout ce qui est simple est fade...   

                                     renderedcontent  replycount  \
0  @H_Soufiane_dz @defense_news نعم وهوا كذالك ال...         0.0   
1                      Attaque Defense Attal❤️❤️🇩🇿🇩🇿         0.0   
2  Conditions générales d'utilisation (CGU) defen...         0.0   
3  @statmuse 24.5 ppg\n8.9 rpg\n2.1 bpg\n52/38/92...         0.0   
4  @Desir_Evasion Tout ce qui est simple est fade...         0.0   

   retweetcount  likecount  quotecount  \
0           0.0        0.0         0.0   
1           0.0        0.0         0.0   
2           0.0        0.0         0.0   
3           0.0        3.0         0.0   
4           0.0        0.0         0.0   

                                                 url lang  ...  \
0  https://twitter.com/amar_khedairia/status/1557...   ar  ...   
1  https://twitter.com/RayanLhd/status/1147958363...   pt  ...   
2  https://twitter.com/benmecheriyacin/status/125...   fr  ...   
3  https://twitter.com/bilel_fetouri/status/15602...   en  ...   
4  https://twitter.com/linda_belkaid/status/95484...   fr  ...   

               user_id  user_location  \
0           4371399077        Algeria   
1            587736375  Paris, France   
2            483636088        algérie   
3  1106949086102597632         annaba   
4   925345775672061953              💖   

                                         description followersCount  \
0  someone who want to enjoy the life  way it's  ...              3   
1                                                               618   
2                                                                86   
3       🇩🇿\n#MFFL\n#Real_Madrid \n#Trust_the_process             14   
4  Il ne faut pas juger les hommes sur une seule ...           2707   

  friendsCount statusesCount favouritesCount protected  \
0          157           299              60     False   
1          482         61245            1286     False   
2         1269         29451              96     False   
3          115           825             938     False   
4         1325         20789           15449     False   

                        mentions search_word  
0  [H_Soufiane_dz, defense_news]         Yes  
1                             []         Yes  
2                 [Defense_gouv]         Yes  
3                     [statmuse]         Yes  
4                [Desir_Evasion]         Yes  

[5 rows x 30 columns]

## Save the File

> Create file Name

In [35]:
#generate a filename 
name = f"african_command_center_tweets"

#get todays date
today = datetime.now()

# format the dates
formated_date = today.strftime("%d_%b").lower()

#extension
extension = ".xlsx"

#generate the name
new_filename = name+"_"+formated_date
old_filename = name+"_"+formated_date+"_"+"oldfile"
print(old_filename ,"\n", new_filename)

african_command_center_tweets_26_aug_oldfile 
 african_command_center_tweets_26_aug


> Write data to Postgresql

In [18]:
#create the connection 

db_host = 'research-dev-db.cluster-c30rc84jwwhk.us-east-2.rds.amazonaws.com'
# db_host = '192.168.8.221'
db_port = 5432
db_password = 'researchpassword'
db = 'postgres'
db_user = 'postgres'


def psql_insert_copy(table, conn, keys, data_iter):
    # gets a DBAPI connection that can provide a cursor
    dbapi_conn = conn.connection
    with dbapi_conn.cursor() as cur:
        s_buf = StringIO()
        writer = csv.writer(s_buf)
        writer.writerows(data_iter)
        s_buf.seek(0)

        columns = ', '.join('"{}"'.format(k) for k in keys)
        if table.schema:
            table_name = '{}.{}'.format(table.schema, table.name)
        else:
            table_name = table.name

        sql = 'COPY {} ({}) FROM STDIN WITH CSV'.format(
            table_name, columns)
        cur.copy_expert(sql=sql, file=s_buf)

engine = create_engine(f'postgresql://{db_user}:{db_password}@{db_host}:{db_port}/{db}')

#write the data if the table exists , replace the data
try:
    data.to_sql(new_filename, engine, method=psql_insert_copy, if_exists='replace')
except Exception as e:
    print(f'The error is: {str(e)}')
    pass

> write the african countries cities

In [19]:
#write the data if the table exists , replace the data
table_name = "african_countries_towns_and_cities"

#write the data into db
try:
    coordinates_df.to_sql(table_name, engine, method=psql_insert_copy, if_exists='replace')
except Exception as e:
    print(f'The error is: {str(e)}')
    pass

> Rename file if present in the directory 

In [20]:
#rename the file if is in directory 
try:
  os.rename(old_filename+'.xlsx', new_filename+'xlsx')
except Exception as e:
  print(f"The error is: {str(e)}")
  pass

The error is: [WinError 2] The system cannot find the file specified: 'african_command_center_tweets_26_aug_oldfile.xlsx' -> 'african_command_center_tweets_26_augxlsx'


> Save the File

In [21]:
#write the file
try:
    data.to_excel(new_filename+'.xlsx', sheet_name = 'tweets data', index = False)
#     coordinates_df.to_excel("african cities coordinates"+'.xlsx', sheet_name = 'tweets data', index = False)
except BaseException as e:
    print('-'*20)
    print(f"The error is {str(e)}")
    pass

In [22]:
# #write the file
# try:
# #     data.to_excel(new_filename+'.xlsx', sheet_name = 'tweets data', index = False)
#     coordinates_df.to_excel("african cities coordinates"+'.xlsx', sheet_name = 'tweets data', index = False)
# except BaseException as e:
#     print('-'*20)
#     print(f"The error is {str(e)}")
#     pass

## Time Spend

In [23]:
#get the time used to proccess the data
end_time = datetime.now()
duration = end_time - start_time
print(f"The stopped at: {end_time} '\n' Started at: {end_time} '\n' and took {duration} to run")

The stopped at: 2022-08-26 04:34:45.556083 '
' Started at: 2022-08-26 04:34:45.556083 '
' and took 2 days, 7:47:54.263342 to run
